## Convert _P.meandrina_ GFF to GTF

_P.meandrina_ GFF (and genome files) were originally obtained from here: 

http://cyanophora.rutgers.edu/Pocillopora_meandrina/

#### Notebook relies on:

- [GffRead](https://github.com/gpertea/gffread)

### List computer specs

In [1]:
%%bash
echo "TODAY'S DATE:"
date
echo "------------"
echo ""
#Display operating system info
lsb_release -a
echo ""
echo "------------"
echo "HOSTNAME: "; hostname 
echo ""
echo "------------"
echo "Computer Specs:"
echo ""
lscpu
echo ""
echo "------------"
echo ""
echo "Memory Specs"
echo ""
free -mh

TODAY'S DATE:
Fri May 19 12:45:28 PM PDT 2023
------------

Distributor ID:	Ubuntu
Description:	Ubuntu 22.04.2 LTS
Release:	22.04
Codename:	jammy

------------
HOSTNAME: 
computer

------------
Computer Specs:

Architecture:                    x86_64
CPU op-mode(s):                  32-bit, 64-bit
Address sizes:                   45 bits physical, 48 bits virtual
Byte Order:                      Little Endian
CPU(s):                          4
On-line CPU(s) list:             0-3
Vendor ID:                       GenuineIntel
Model name:                      Intel(R) Core(TM) i9-10885H CPU @ 2.40GHz
CPU family:                      6
Model:                           165
Thread(s) per core:              1
Core(s) per socket:              1
Socket(s):                       4
Stepping:                        2
BogoMIPS:                        4800.01
Flags:                           fpu vme de pse tsc msr pae mce cx8 apic sep mtrr pge mca cmov pat pse36 clflush mmx fxsr sse sse2 ss syscall

No LSB modules are available.


### Set variables
- `%env` indicates a bash variable

- without `%env` is Python variable

In [2]:
# Set directories, input/output files
%env data_dir=/home/sam/data/P_meandrina/genomes
%env analysis_dir=/home/sam/analyses/20230519-pmea-gff_to_gtf
analysis_dir="20230519-pmea-gff_to_gtf"

# Input files (from NCBI)
%env gff=Pocillopora_meandrina_HIv1.genes.gff3

# URL of file directory
%env url=owl:/volume1/web/halfshell/genomic-databank

# Output file(s)
%env gtf=Pocillopora_meandrina_HIv1.genes.gtf


# Set program locations
%env gffread=/home/sam/programs/gffread-0.12.7.Linux_x86_64/gffread

# Set some formatting stuff
%env break_line=--------------------------------------------------------------------------

env: data_dir=/home/sam/data/P_meandrina/genomes
env: analysis_dir=/home/sam/analyses/20230519-pmea-gff_to_gtf
env: gff=Pocillopora_meandrina_HIv1.genes.gff3
env: url=owl:/volume1/web/halfshell/genomic-databank
env: gtf=Pocillopora_meandrina_HIv1.genes.gtf
env: gffread=/home/sam/programs/gffread-0.12.7.Linux_x86_64/gffread
env: break_line=--------------------------------------------------------------------------


### Create analysis directory

In [3]:
%%bash
# Make analysis and data directory, if doesn't exist
mkdir --parents "${analysis_dir}"

mkdir --parents "${data_dir}"

### Download GFF

In [4]:
%%bash
cd "${data_dir}"

rsync "${url}/${gff}" .


ls -ltrh "${gff}"

-rw-r--r-- 1 sam sam 55M May 19 12:45 Pocillopora_meandrina_HIv1.genes.gff3


### Examine GFF

In [5]:
%%bash
head -n 20 "${data_dir}"/"${gff}"

Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	transcript	9649	18299	.	-	.	ID=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	CDS	9649	9706	.	-	1	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	9649	9706	.	-	1	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	CDS	10225	10352	.	-	0	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	10225	10352	.	-	0	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	CDS	11330	11655	.	-	2	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	11330	11655	.	-	2	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	CDS	11902	11972	.	-	1	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS

#### Count unique number of fields

This identifies if there are rows with >9 fields (which there shouldn't be in a [GFF3](http://gmod.org/wiki/GFF3)).

In [6]:
%%bash
# Capture number of fields (NF) in each row in array.
field_count_array=($(awk -F "\t" '{print NF}' "${data_dir}/${gff}" | sort --unique))

# Check array contents
echo "List of number of fields in ${data_dir}/${gff}:"
echo ""
for field_count in "${field_count_array[@]}"
do
  echo "${field_count}"
done

echo ""
echo "${break_line}"
echo ""

# Preview of each line "type" with a given number of fields
# Check array contents
echo ""
for field_count in "${field_count_array[@]}"
do
  echo "Preview of lines with ${field_count} field(s):"
  echo ""
  awk \
    -v field_count="${field_count}" \
    -F "\t" \
    'NF == field_count' \
    "${data_dir}/${gff}" \
    | head
  echo ""
  echo "${break_line}"
  echo ""
done

List of number of fields in /home/sam/data/P_meandrina/genomes/Pocillopora_meandrina_HIv1.genes.gff3:

9

--------------------------------------------------------------------------


Preview of lines with 9 field(s):

Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	transcript	9649	18299	.	-	.	ID=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	CDS	9649	9706	.	-	1	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	9649	9706	.	-	1	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	CDS	10225	10352	.	-	0	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	10225	10352	.	-	0	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	CDS	11330	11655	.	-	2	Parent=Pocillopora_meandrina_HIv1___TS.g23774.t1
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	11330	11655	.	-

### Convert GFF to GTF

In [7]:
%%bash
cd "${data_dir}"

${gffread} -E \
${data_dir}/"${gff}" -T \
1> ${analysis_dir}/"${gtf}" \
2> ${analysis_dir}/gffread-gff_to_gtf.stderr

### Inspect GTF

In [8]:
%%bash
head ${analysis_dir}/"${gtf}"

Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	transcript	9649	18299	.	-	.	transcript_id "Pocillopora_meandrina_HIv1___TS.g23774.t1"; gene_id "Pocillopora_meandrina_HIv1___TS.g23774.t1"
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	9649	9706	.	-	.	transcript_id "Pocillopora_meandrina_HIv1___TS.g23774.t1";
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	10225	10352	.	-	.	transcript_id "Pocillopora_meandrina_HIv1___TS.g23774.t1";
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	11330	11655	.	-	.	transcript_id "Pocillopora_meandrina_HIv1___TS.g23774.t1";
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	11902	11972	.	-	.	transcript_id "Pocillopora_meandrina_HIv1___TS.g23774.t1";
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	12137	12195	.	-	.	transcript_id "Pocillopora_meandrina_HIv1___TS.g23774.t1";
Pocillopora_meandrina_HIv1___Sc0000007	AUGUSTUS	exon	15864	15925	.	-	.	transcript_id "Pocillopora_meandrina_HIv1___TS.g23774.t1";
Pocillopora_meandrina_HIv1___Sc0000

### Generate checksum(s)

In [9]:
%%bash
cd "${analysis_dir}"

for file in *
do
  md5sum "${file}" | tee --append checksums.md5
done

3b8858bc09d0c5e630b917d9177fad23  gffread-gff_to_gtf.stderr
638abc4f5f115e7a32731ad24cc558fd  Pocillopora_meandrina_HIv1.genes.gtf


### Document GffRead program options

In [10]:
%%bash
${gffread} -h

gffread v0.12.7. Usage:
gffread [-g <genomic_seqs_fasta> | <dir>] [-s <seq_info.fsize>] 
 [-o <outfile>] [-t <trackname>] [-r [<strand>]<chr>:<start>-<end> [-R]]
 [--jmatch <chr>:<start>-<end>] [--no-pseudo] 
 [-CTVNJMKQAFPGUBHZWTOLE] [-w <exons.fa>] [-x <cds.fa>] [-y <tr_cds.fa>]
 [-j ][--ids <IDs.lst> | --nids <IDs.lst>] [--attrs <attr-list>] [-i <maxintron>]
 [--stream] [--bed | --gtf | --tlf] [--table <attrlist>] [--sort-by <ref.lst>]
 [<input_gff>] 

 Filter, convert or cluster GFF/GTF/BED records, extract the sequence of
 transcripts (exon or CDS) and more.
 By default (i.e. without -O) only transcripts are processed, discarding any
 other non-transcript features. Default output is a simplified GFF3 with only
 the basic attributes.
 
Options:
 --ids discard records/transcripts if their IDs are not listed in <IDs.lst>
 --nids discard records/transcripts if their IDs are listed in <IDs.lst>
 -i   discard transcripts having an intron larger than <maxintron>
 -l   discard transcripts

CalledProcessError: Command 'b'${gffread} -h\n'' returned non-zero exit status 1.